In [27]:
import numpy as np
import tensorflow as tf

In [28]:
tf.logging.set_verbosity(tf.logging.INFO)

In [29]:
#Let's create the model
def cnn_model_fn(features, labels, mode):
    #Input Lapyer
    input_layer = tf.reshape(features["x"], [-1,28,28,1]) 
    #batch_size=-1, the dimension should be dynamically computed. based on number of input values in features["x"]                                                          
    
    #CN layer 1
    conv1 = tf.layers.conv2d(inputs=input_layer, filters=32, kernel_size=[5,5], padding="same", activation=tf.nn.relu)
    
    #Pooling layer1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2,2], strides=2)
    
    #CN layer 2
    conv2 = tf.layers.conv2d(inputs=pool1, filters=64, kernel_size=[5,5], padding="same", activation=tf.nn.relu)
    
    #pool layer2
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2,2], strides=2)
    
    #Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7*7*64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    #Drop-out will only be applied if we are in training mode, mode==tf.estimator.ModKeys.TRAIN
    
    #Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)
    #This has shape of batch_size(that -1),10
    #This returns batch-size,10 dimensional tensor
    
    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1), #Simply findout which one has the maximum of 10
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor") #This one is the softmax
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    #Estimator spec which says for this mode these are the predictions

    #Calculate loss - LOSS
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    # Configure the Training Op (for TRAIN mode) Optimizer
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode) Evalution Matric
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


In [30]:
def main(unused_arg):
    #Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images #returns an np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    #Creating the extimator
    mnist_classiier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_cnn_model")
    
    #Setting up some logging
    tensor_to_log = {"probabilities":"softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensor_to_log, every_n_iter=50)
    #We store a dict of the tensors we want to log in tensor_to_log
    #Each key is a label of our choice that will be printed in the log output, 
    #and the corresponding label is the name of a Tensor in the TensorFlow graph. 
    #Here, our probabilities can be found in softmax_tensor
    
    #Setting up some logging
    tensor_to_log = {"probabilities":"softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensor_to_log, every_n_iter=50)
    #We store a dict of the tensors we want to log in tensor_to_log
    #Each key is a label of our choice that will be printed in the log output, 
    #and the corresponding label is the name of a Tensor in the TensorFlow graph. 
    #Here, our probabilities can be found in softmax_tensor
    
    #Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(x={"x":train_data}, y=train_labels, batch_size=100, num_epochs=None, shuffle=True)
    mnist_classiier.train(input_fn=train_input_fn, steps=20000, hooks=[logging_hook])
    
    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

if __name__ == "__main__":
    tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_cnn_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f1ae7af2438>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replica

INFO:tensorflow:loss = 2.30513, step = 1
INFO:tensorflow:probabilities = [[ 0.10851131  0.103433    0.09327819  0.10509957  0.09347991  0.09754412
   0.10407658  0.11070056  0.08454646  0.09933034]
 [ 0.104031    0.10788596  0.1002327   0.10465189  0.09015256  0.1012001
   0.09682029  0.10068598  0.08777503  0.10656454]
 [ 0.09880885  0.10841052  0.08344655  0.11043013  0.10574773  0.10525434
   0.09928473  0.11185335  0.07543106  0.10133275]
 [ 0.10714221  0.11405281  0.09385014  0.10647709  0.10420563  0.08594888
   0.10039204  0.10015934  0.09036809  0.09740378]
 [ 0.09817374  0.11538974  0.08309544  0.10645749  0.10255458  0.09932756
   0.10359604  0.10694846  0.08230197  0.10215496]
 [ 0.098684    0.10931271  0.09710749  0.10180107  0.09219911  0.10343915
   0.10138158  0.10540891  0.09101393  0.0996521 ]
 [ 0.12361037  0.10126607  0.09940679  0.10328406  0.08559489  0.09536844
   0.10021208  0.10172314  0.08721665  0.10231754]
 [ 0.10181435  0.10325825  0.09935088  0.10533316  0.

INFO:tensorflow:global_step/sec: 63.7925
INFO:tensorflow:probabilities = [[ 0.12163439  0.11221217  0.10487962  0.09312121  0.09382247  0.10280727
   0.09443936  0.0900319   0.0883332   0.09871835]
 [ 0.11305349  0.09548577  0.08411926  0.11129091  0.08829845  0.11506961
   0.09292456  0.10741006  0.09820542  0.09414247]
 [ 0.11111629  0.10272728  0.09201454  0.11013856  0.09254442  0.10114639
   0.09648915  0.1037643   0.09191328  0.09814581]
 [ 0.10608744  0.10041818  0.08894307  0.10553438  0.10883537  0.09766395
   0.10430308  0.10008002  0.09400398  0.09413054]
 [ 0.10314115  0.1026796   0.08089474  0.10634563  0.11461776  0.10215105
   0.09753606  0.10989828  0.08966972  0.09306595]
 [ 0.10795327  0.09918513  0.10344468  0.10100416  0.10963162  0.08814654
   0.10342528  0.10947344  0.08896035  0.08877553]
 [ 0.1039584   0.10346255  0.09338457  0.11630027  0.0977819   0.10220151
   0.09353051  0.10381193  0.09176372  0.09380464]
 [ 0.10908371  0.10019407  0.08477725  0.10843316  0

INFO:tensorflow:loss = 2.29393, step = 101 (1.569 sec)
INFO:tensorflow:probabilities = [[ 0.09949035  0.09722511  0.09954914  0.11370497  0.09541951  0.09658412
   0.095881    0.10052439  0.09377775  0.10784366]
 [ 0.10703468  0.11933131  0.0821145   0.09251662  0.09930637  0.10433128
   0.10418889  0.10063674  0.09514442  0.09539519]
 [ 0.1158729   0.10199217  0.09900927  0.10494043  0.10346483  0.10715715
   0.08970932  0.09107238  0.09423481  0.09254673]
 [ 0.09543844  0.1045525   0.09923762  0.11099747  0.09167681  0.09559947
   0.10119396  0.09754241  0.09674017  0.10702112]
 [ 0.09552568  0.10042209  0.08747616  0.10802273  0.10204854  0.10833897
   0.10307109  0.10629744  0.08543963  0.10335773]
 [ 0.10278391  0.10005873  0.09067965  0.10715956  0.09458438  0.10202289
   0.09645045  0.10391306  0.09544726  0.10690009]
 [ 0.09969398  0.11957645  0.08570262  0.09794638  0.10580213  0.10107859
   0.09791148  0.09887087  0.09109687  0.10232066]
 [ 0.11157395  0.10043561  0.0854666  

INFO:tensorflow:global_step/sec: 72.1991
INFO:tensorflow:probabilities = [[ 0.09540748  0.11203603  0.09058522  0.10156315  0.09435963  0.10628334
   0.0956042   0.10739078  0.096824    0.09994613]
 [ 0.10491379  0.09233765  0.09042828  0.10096255  0.11241099  0.09001065
   0.10446244  0.10271445  0.09723397  0.10452518]
 [ 0.11401299  0.09174969  0.08579681  0.1097818   0.09721419  0.09641552
   0.09255783  0.10515982  0.0934549   0.11385643]
 [ 0.10369496  0.1089963   0.08788212  0.10774006  0.09928125  0.0981797
   0.10230292  0.09922975  0.0975915   0.09510142]
 [ 0.10380278  0.09466882  0.08903148  0.1015415   0.09994831  0.0979072
   0.10532993  0.1061618   0.10400813  0.0976    ]
 [ 0.11712252  0.11365896  0.0986378   0.09729417  0.11042386  0.08662599
   0.09404916  0.09687711  0.08699254  0.09831788]
 [ 0.099626    0.09751413  0.10299972  0.10530013  0.09751064  0.09978505
   0.10616743  0.09731405  0.09051108  0.10327178]
 [ 0.09839261  0.11334325  0.09059012  0.10337188  0.0

...

INFO:tensorflow:loss = 0.271928, step = 19801 (1.343 sec)
INFO:tensorflow:probabilities = [[ 0.00382052  0.89552552  0.0025919   0.00186852  0.00115313  0.00067023
   0.01409027  0.00126307  0.07869679  0.00031998]
 [ 0.00003931  0.00000014  0.00001538  0.0000395   0.02757948  0.00006693
   0.00000116  0.00253525  0.00015279  0.9695701 ]
 [ 0.869344    0.00001794  0.00076571  0.00675776  0.00038067  0.00075884
   0.00142966  0.03271874  0.00007259  0.08775403]
 [ 0.00000303  0.00000534  0.00103155  0.000246    0.00000142  0.00157149
   0.00000113  0.00000108  0.99712425  0.00001474]
 [ 0.00000757  0.00000116  0.00001041  0.00095199  0.00400864  0.00105506
   0.00000012  0.05541538  0.00135992  0.93718982]
 [ 0.0000193   0.00000056  0.00002222  0.00000282  0.99629164  0.00007366
   0.00012197  0.00070998  0.00002917  0.00272872]
 [ 0.00000154  0.          0.0000001   0.00000026  0.00105556  0.00000248
   0.00000002  0.00007324  0.0000717   0.99879503]
 [ 0.00011003  0.00001629  0.000087

INFO:tensorflow:global_step/sec: 74.5853
INFO:tensorflow:probabilities = [[ 0.00024333  0.00001738  0.00016695  0.0000036   0.0000573   0.00116456
   0.99831343  0.00000002  0.0000333   0.00000009]
 [ 0.00035037  0.00000058  0.00001887  0.02475729  0.00003417  0.88439614
   0.00000852  0.00003574  0.08763801  0.00276032]
 [ 0.00002295  0.00001644  0.00002678  0.00001527  0.00483015  0.00035937
   0.00000189  0.4127984   0.00075712  0.58117163]
 [ 0.0000914   0.00002019  0.00023583  0.00000034  0.00002276  0.00006548
   0.99949467  0.0000004   0.00006506  0.00000383]
 [ 0.00024632  0.06973677  0.02540184  0.87012887  0.00034957  0.00094515
   0.00005343  0.01478852  0.01661129  0.00173826]
 [ 0.00000117  0.99791604  0.00031349  0.00011876  0.00006667  0.00010344
   0.00009448  0.00006981  0.00127042  0.00004566]
 [ 0.00001839  0.99617755  0.00029872  0.00145511  0.00024516  0.00004222
   0.000099    0.00118955  0.00036663  0.00010757]
 [ 0.99975842  0.0000004   0.00001229  0.00000024  0

INFO:tensorflow:loss = 0.0688112, step = 19901 (1.341 sec)
INFO:tensorflow:probabilities = [[ 0.0000083   0.00000601  0.99961495  0.00012113  0.00000052  0.00000041
   0.00000578  0.00000065  0.00024205  0.00000019]
 [ 0.99905986  0.00000002  0.00009452  0.00000964  0.00000004  0.00018879
   0.00005592  0.00000548  0.00057335  0.0000124 ]
 [ 0.00001202  0.00000718  0.00006482  0.00072324  0.0000029   0.0011488
   0.00001544  0.0000061   0.99800986  0.00000959]
 [ 0.00000969  0.0001117   0.00108874  0.00013482  0.99761093  0.0000819
   0.00026703  0.00005909  0.00000252  0.00063365]
 [ 0.00365693  0.07031691  0.06640957  0.03173254  0.00022102  0.00294651
   0.00066691  0.00492135  0.81659281  0.00253544]
 [ 0.00058737  0.90687245  0.00652126  0.03559273  0.00748221  0.00745848
   0.0045106   0.0026826   0.02255628  0.00573612]
 [ 0.00002126  0.99649769  0.00031507  0.00025377  0.00015024  0.000058
   0.0003897   0.00163962  0.00061091  0.00006371]
 [ 0.99142683  0.00000024  0.00003285 

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_cnn_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.178587.


NameError: name 'mnist_classifier' is not defined